In [83]:
import pandas as pd
import numpy as np
import plotly.express as px

## Model 1

$$\frac{dR}{dt} = r(1-R/K)R - \frac{zR}{R+S}C$$

$$\frac{dC}{dt} = \frac{bzR}{R+S}C - mC$$

$$R_{crit} = \frac{mS}{bz-m}$$

In [87]:
def simulate(R, C, N, dt, params):
    # consumer params
    b = params['b']
    z = params['z']
    S = params['S']
    m = params['m']

    assert b * z - m > 0, 'Mortality is too high for the consumer to survive'

    # resource params
    K = params['K']
    r = params['r']

    R_array, C_array = [], []
    dR_array, dC_array = [], []
    for _ in range(N):
        R_array.append(R)
        C_array.append(C)
        dR = (r * (1 - R/K) * R - z * R / (R + S) * C) * dt 
        dC = (b * z * R / (R + S) * C - m * C) * dt 
        dR_array.append(dR)
        dC_array.append(dC)

        R = max(0, R + dR)
        C = max(0, C + dC)
    
    return pd.DataFrame(
        {'R': R_array, 'C': C_array, 'time': np.arange(N) * dt, 'dR': dR_array, 'dC': dC_array}
    )

params = {
    'b': 0.5, 'z': 0.5, 'S': 10, 'm': 0.2,
    'K': 100, 'r': 0.1
}
R = params['S'] / (params['b'] * params['z'] - params['m'])
print(R)
results = simulate(R, 1, 10000, 0.1, params)
fig = px.line(results, x='time', y=['C', 'R'])
fig.show()

200.00000000000006


In [117]:
params = {
    'b': 0.6, 'z': 0.6, 'S': 25, 'm': 0.23,
    'K': 100, 'r': 0.5
}
R = params['m'] * params['S'] / (params['b'] * params['z'] - params['m'])
print(R)
results = simulate(R, 1, 10000, 0.1, params)
fig = px.line(results, x='time', y=['R', 'C'])
fig.show()

44.23076923076924


In [80]:
params = {
    'b': 0.75, 'z': 0.75, 'S': 10, 'm': 0.5125,
    'K': 100, 'r': 0.1
}
R = params['S'] / (params['b'] * params['z'] - params['m'])
print(R)
results = simulate(R, 1, 10000, 0.1, params)
fig = px.line(results, x='time', y=['dC'])
fig.show()

199.99999999999983


1. The consumer is able to convert the resource so well it reaches very high levels and therefore decimates the resource population (thereby decimating itself).
2. The resource gets to such high levels it supports a population capable of ruining itself. 

Ways to stabilize the system (into oscillations that don't decimate the populations):

1. Drop $K$ so the maximum $C$ possible drops.
2. Drop $b$ or $z$ or raise $m$ so the conversion rate of $C$ drops. 
3. Raise $S$ so that the $C$ conversion drops. 

Changing $r$ simply seems to have the effect of changing how quickly the system cycles. 

In [75]:
0.75 * 0.75 - 0.5125

0.5625

## Model 2

$$\frac{dR}{dt} = r(1-R/K)R - \frac{z}{1+\alpha F}C$$

$$\frac{dC}{dt} = \frac{bz}{1+\alpha F}C - mC$$

One question now is, given a certain $R$ what's the amount of resource that can be extracted by $C$? Because this should be the main difference between this and the last model.

In [124]:
C = np.arange(0, 1000, 0.1)
R = 2

Y = 0.6 / (1 + 0.6 * C / R) * C

fig = px.line(x=C, y=Y)
fig.show()

The answer is that the limit is:

$$\frac{z}{\alpha}R$$

Now obviously this can be greater than $R$ but that's alright because in theory the consumer can extract the full resource
quickly or slowly. The main point here is that adding more $C$ does not create limitless growth in the extraction speed. 

In [227]:
def simulate(R, C, N, dt, params):
    # consumer params
    b = params['b']
    z = params['z']
    alpha = params['alpha']
    m = params['m']

    assert b * z - m > 0, 'Mortality is too high for the consumer to survive'

    # resource params
    K = params['K']
    r = params['r']

    R_array, C_array, F_array = [], [], []
    dR_array, dC_array = [], []
    for _ in range(N):
        F = C / R
        R_array.append(R)
        C_array.append(C)
        F_array.append(F)
        dR = (r * (1 - R/K) * R - z / (1 + alpha * F) * C) * dt 
        dC = (b * z / (1 + alpha * F) * C - m * C) * dt 
        dR_array.append(dR/R)
        dC_array.append(dC)

        R = max(0, R + dR)
        C = max(0, C + dC)
    
    return pd.DataFrame(
        {
            'R': R_array, 'C': C_array, 
            'time': np.arange(N) * dt, 'F': F_array,
            'dR': dR_array, 'dC': dC_array
        }
    )

params = {
    'b': 0.5, 'z': 0.55, 'alpha': 0.45, 'm': 0.2,
    'K': 100, 'r': 0.6
}

#print(params['z'] * params['b'] / params['m'], 1 + params['alpha'] * params['r'] / (params['z'] - params['r'] * params['alpha']))
#print(params['z'] - params['r'] * params['alpha'])

gamma = params['r'] / (params['z'] - params['r'] * params['alpha'])
print(params['m'] - params['z'] * params['b'] / (1 + gamma * params['alpha']))
print(gamma)
print(params['r'] - params['z'] / params['alpha'])
FC = (params['z'] * params['b'] - params['m']) / (params['alpha'] * params['m'])
#print(FC)
results = simulate(10, 22, 20000, 0.1, params)
fig = px.line(results, x='time', y=['R', 'C'])
fig.show()

0.06
2.142857142857143
-0.6222222222222223
